In [1]:
import torch
torch.__version__

'2.4.0'

In [2]:
import torch
torch.cuda.is_available()

False

In [3]:
# 检查能否苹果芯片加速
print(torch.backends.mps.is_available())

True


In [5]:
tensor1d = torch.tensor([1, 2, 3])
print(tensor1d.dtype)

floatvec = torch.tensor([1.0, 2.0, 3.0])
print(floatvec.dtype)

torch.int64
torch.float32


In [7]:
floatvec = tensor1d.to(torch.float64)
print(floatvec.dtype)

torch.float64


In [18]:
tensor2d = torch.tensor([[1, 2, 3],[4,5,6]])
print('tensor2d:')
print(tensor2d)

print('\nsize:')
print(tensor2d.shape)

print('\nreshape:')
print(tensor2d.reshape(3, 2))
print(tensor2d.reshape(3, 2).shape)

print('\ntranspose:')
print(tensor2d.T)

tensor2d:
tensor([[1, 2, 3],
        [4, 5, 6]])

size:
torch.Size([2, 3])

reshape:
tensor([[1, 2],
        [3, 4],
        [5, 6]])
torch.Size([3, 2])

transpose:
tensor([[1, 4],
        [2, 5],
        [3, 6]])


In [20]:
print(tensor2d.matmul(tensor2d.T))
print(tensor2d @ tensor2d.T)

tensor([[14, 32],
        [32, 77]])
tensor([[14, 32],
        [32, 77]])


In [27]:
import torch.nn.functional as F
from torch.autograd import grad

# 定义变量
y = torch.tensor([1.0])
x1 = torch.tensor([1.1])
w1 = torch.tensor([2.2], requires_grad=True)
b = torch.tensor([0.0], requires_grad=True)

# 前向传播
z = x1 * w1 + b
a = torch.sigmoid(z)
loss = F.binary_cross_entropy(a, y)
print("loss: ", loss)

# 手动计算梯度
grad_L_w1 = grad(loss, w1, retain_graph=True)
grad_L_b = grad(loss, b, retain_graph=True)

# 打印梯度
print("grad_L_w1: ", grad_L_w1)
print("grad_L_b: ", grad_L_b)

# 使用自动求导计算梯度
loss.backward()
print("w1.grad: ", w1.grad)
print("b.grad: ", b.grad)

loss:  tensor(0.0852, grad_fn=<BinaryCrossEntropyBackward0>)
grad_L_w1:  (tensor([-0.0898]),)
grad_L_b:  (tensor([-0.0817]),)
w1.grad:  tensor([-0.0898])
b.grad:  tensor([-0.0817])


In [28]:
class NeuralNetwork(torch.nn.Module):
    def __init__(self, num_inputs, num_outputs):
        super().__init__()

        self.layers = torch.nn.Sequential(
            # 1st hidden layer
            torch.nn.Linear(num_inputs, 30),
            torch.nn.ReLU(),

            # 2nd hidden layer
            torch.nn.Linear(30, 20),
            torch.nn.ReLU(),

            # output layer
            torch.nn.Linear(20, num_outputs),
        )

    def forward(self, x):
        logits = self.layers(x)
        return logits

In [29]:
model = NeuralNetwork(50, 3)
print(model)

NeuralNetwork(
  (layers): Sequential(
    (0): Linear(in_features=50, out_features=30, bias=True)
    (1): ReLU()
    (2): Linear(in_features=30, out_features=20, bias=True)
    (3): ReLU()
    (4): Linear(in_features=20, out_features=3, bias=True)
  )
)


In [31]:
num_params = sum(p.numel() for p in model.parameters() if p.requires_grad)
print("Total number of trainable model parameters:", num_params)

Total number of trainable model parameters: 2213


In [35]:
print(model.layers[0].requires_grad_)
print(model.layers[0].bias.shape)
print(model.layers[0].bias)
print(model.layers[0].weight.shape)
print(model.layers[0].weight)

<bound method Module.requires_grad_ of Linear(in_features=50, out_features=30, bias=True)>
torch.Size([30])
Parameter containing:
tensor([-0.1171, -0.0217, -0.1199, -0.0963,  0.1263, -0.0341, -0.1333,  0.0423,
        -0.1356, -0.1024, -0.0755,  0.1048, -0.0823,  0.1001,  0.0479, -0.0029,
        -0.0903, -0.1398, -0.1182, -0.0729,  0.0860,  0.0688, -0.1325,  0.0761,
         0.1036, -0.0603, -0.1414, -0.0402,  0.0116,  0.1230],
       requires_grad=True)
torch.Size([30, 50])
Parameter containing:
tensor([[-0.0429,  0.1381,  0.0244,  ...,  0.0194, -0.0300,  0.0354],
        [-0.0794,  0.1391, -0.1369,  ...,  0.0286,  0.1396,  0.1343],
        [ 0.1208,  0.0249, -0.1211,  ..., -0.0616,  0.1108, -0.1159],
        ...,
        [-0.1237, -0.0588, -0.1023,  ..., -0.0643,  0.0637,  0.0125],
        [-0.1161, -0.1299,  0.1352,  ..., -0.1357, -0.0670,  0.0172],
        [-0.1025, -0.0604, -0.0470,  ..., -0.1188,  0.0495,  0.0246]],
       requires_grad=True)


In [37]:
torch.manual_seed(123)
X = torch.rand((1, 50))
out = model(X)
print(out)

tensor([[0.0129, 0.1710, 0.2290]], grad_fn=<AddmmBackward0>)


In [39]:
with torch.no_grad():
    out = model(X)
print(out)

tensor([[0.0129, 0.1710, 0.2290]])


In [40]:
with torch.no_grad():
    out = torch.softmax(model(X), dim=1)
print(out)

tensor([[0.2930, 0.3432, 0.3637]])


In [41]:
with torch.no_grad():
    out = torch.softmax(model(X), dim=1)
print(out)

tensor([[0.2930, 0.3432, 0.3637]])


In [42]:
# training data
X_train = torch.tensor([
    [-1.2, 3.1],
    [-0.9, 2.9],
    [-0.5, 2.6],
    [2.3, -1.1],
    [2.7, -1.5]
])
y_train = torch.tensor([0, 0, 0, 1, 1])

# test data
X_test = torch.tensor([
    [-0.8, 2.8],
    [2.6, -1.6],
])
y_test = torch.tensor([0, 1])

In [46]:
print(len(train_ds))
print(len(test_ds))

5
2


In [61]:
from torch.utils.data import DataLoader

torch.manual_seed(123)

train_loader = DataLoader(
    dataset=train_ds,
    batch_size=2,
    shuffle=True,
    num_workers=0
)

test_loader = DataLoader(
    dataset=test_ds,
    batch_size=2,
    shuffle=False,
    num_workers=0
)

for idx, (x, y) in enumerate(train_loader):
    print(f"Batch {idx+1}:", x, y)

Batch 1: tensor([[ 2.3000, -1.1000],
        [-0.9000,  2.9000]]) tensor([1, 0])
Batch 2: tensor([[-1.2000,  3.1000],
        [-0.5000,  2.6000]]) tensor([0, 0])
Batch 3: tensor([[ 2.7000, -1.5000]]) tensor([1])


In [62]:
torch.manual_seed(123)

train_loader = DataLoader(
    dataset=train_ds,
    batch_size=2,
    shuffle=True,
    num_workers=0,
    drop_last=True,
)

for idx, (x, y) in enumerate(train_loader):
    print(f"Batch {idx+1}:", x, y)

Batch 1: tensor([[ 2.3000, -1.1000],
        [-0.9000,  2.9000]]) tensor([1, 0])
Batch 2: tensor([[-1.2000,  3.1000],
        [-0.5000,  2.6000]]) tensor([0, 0])


In [64]:
import torch.nn.functional as F

# Set the random seed for reproducibility
torch.manual_seed(123)

# Define the model; the dataset has two features and two classes
model = NeuralNetwork(num_inputs=2, num_outputs=2)

# Define the optimizer and specify the model parameters to optimize and the learning rate
optimizer = torch.optim.SGD(model.parameters(), lr=0.5)

# Set the number of training epochs
num_epochs = 3
for epoch in range(num_epochs):
    # Set the model to training mode
    model.train()
    for batch_idx, (features, labels) in enumerate(train_loader):
        # Perform forward pass to compute model outputs
        logits = model(features)

        # Compute the cross-entropy loss
        loss = F.cross_entropy(logits, labels)

        # Clear gradients from the previous iteration
        optimizer.zero_grad()

        # Perform backpropagation to compute gradients
        loss.backward()

        # Update the model parameters using the computed gradients
        optimizer.step()

        # Log the current epoch, batch, and training loss
        print(f"Epoch: {epoch+1:03d}/{num_epochs:03d} "
              f"| Batch {batch_idx:03d}/{len(train_loader):03d} "
              f"| Train Loss: {loss:.2f}")

# Set the model to evaluation mode
model.eval()

# Optional: Insert model evaluation code here
# Insert optional model evaluation code

Epoch: 001/003 | Batch 000/002 | Train Loss: 0.75
Epoch: 001/003 | Batch 001/002 | Train Loss: 0.65
Epoch: 002/003 | Batch 000/002 | Train Loss: 0.44
Epoch: 002/003 | Batch 001/002 | Train Loss: 0.13
Epoch: 003/003 | Batch 000/002 | Train Loss: 0.03
Epoch: 003/003 | Batch 001/002 | Train Loss: 0.00


NeuralNetwork(
  (layers): Sequential(
    (0): Linear(in_features=2, out_features=30, bias=True)
    (1): ReLU()
    (2): Linear(in_features=30, out_features=20, bias=True)
    (3): ReLU()
    (4): Linear(in_features=20, out_features=2, bias=True)
  )
)

In [65]:
num_params = sum(p.numel() for p in model.parameters() if p.requires_grad)
print("Total number of trainable model parameters:", num_params)

Total number of trainable model parameters: 752


In [66]:
model.eval()
with torch.no_grad():
    outputs = model(X_train)
print(outputs)

tensor([[ 2.8569, -4.1618],
        [ 2.5382, -3.7548],
        [ 2.0944, -3.1820],
        [-1.4814,  1.4816],
        [-1.7176,  1.7342]])


In [67]:
torch.set_printoptions(sci_mode=False)
probas = torch.softmax(outputs, dim=1)
print(probas)

tensor([[    0.9991,     0.0009],
        [    0.9982,     0.0018],
        [    0.9949,     0.0051],
        [    0.0491,     0.9509],
        [    0.0307,     0.9693]])


In [68]:
predictions = torch.argmax(probas, dim=1)
print(predictions)

tensor([0, 0, 0, 1, 1])


In [70]:
predictions == y_train

tensor([True, True, True, True, True])

In [71]:
torch.sum(predictions == y_train)

tensor(5)

In [75]:
def compute_accuracy(model, dataloader):
    model = model.eval()
    correct = 0.0
    total_examples = 0

    for idx, (features, labels) in enumerate(dataloader):
        with torch.no_grad():
            logits = model(features)
            # Returns a tensor of True/False values depending on whether the labels match
            predictions = torch.argmax(logits, dim=1)
            compare = labels == predictions
            # The sum operation counts the number of True values.
            correct += torch.sum(compare)
            total_examples += len(compare)

    # The fraction of correct prediction, a value between 0 and 1.
    # .item() returns the value of the tensor as a Python float.
    return (correct / total_examples).item()

print(compute_accuracy(model, train_loader))
print(compute_accuracy(model, test_loader))

1.0
1.0


In [76]:
# save model
torch.save(model.state_dict(), "toy_model.pth")

# load model
my_model = NeuralNetwork(2, 2)
my_model.load_state_dict(torch.load("toy_model.pth"))
print(compute_accuracy(my_model, train_loader))
print(compute_accuracy(my_model, test_loader))

1.0
1.0


/var/folders/dr/_84tyhw97xq0k382v16__h6h0000gn/T/ipykernel_6395/1224051159.py:6: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  my_model.load_state_dict(torch.load("toy_model

In [77]:
print(torch.cuda.is_available())

False
